In [3]:
import napari
import os
from tqdm import tqdm
import numpy as np
from ultrack import MainConfig, load_config, track, to_tracks_layer, tracks_to_zarr
import glob2 as glob
import zarr
import json
import skimage.io as io
import pandas as pd
import umap.umap_ as umap
from sklearn.preprocessing import StandardScaler

# # set parameters
root = "E:\\Nick\\Cole Trapnell's Lab Dropbox\\Nick Lammers\\Nick\\killi_tracker\\"
project_name = "231016_EXP40_LCP1_UVB_300mJ_WT_Timelapse_Raw"
image_dir = os.path.join(root, "built_data", project_name, "")
ds_factor = 2
config_name = "tracking_final.txt"
tracking_folder = config_name.replace(".txt", "")
tracking_folder = tracking_folder.replace(".toml", "")

tracking_directory = os.path.join(root, "built_data", "tracking", tracking_folder, project_name)
snip_directory = os.path.join(root, "built_data", "shape_snips", tracking_folder, project_name)

# load metadata
metadata_file_path = os.path.join(root, "metadata", project_name, "metadata.json")
f = open(metadata_file_path)
metadata = json.load(f)
scale_vec = np.asarray([metadata["ProbPhysicalSizeZ"], metadata["ProbPhysicalSizeY"], metadata["ProbPhysicalSizeX"]])

In [9]:
cell_shape_df = pd.read_csv(os.path.join(tracking_directory, "cell_shape_df.csv"))
cell_shape_df.head()
n_components = 2

np.random.seed(356)

shape_array = cell_shape_df.iloc[:, 2:].to_numpy()

reducer = umap.UMAP(n_components=n_components)
# scaled_shape_array = StandardScaler().fit_transform(shape_array)
shape_embedding = reducer.fit_transform(shape_array)

cell_shape_df["UMAP00"] = shape_embedding[:, 0]
cell_shape_df["UMAP01"] = shape_embedding[:, 1]

In [7]:
import plotly.express as px
fig = px.scatter(cell_shape_df, x="UMAP00", y="UMAP01", color="track_id")
fig.show()

In [8]:
from pyefd import elliptic_fourier_descriptors
import pyefd
shape_i = 0

out = pyefd.reconstruct_contour(shape_array[shape_i, :])

array([[-3.42739171e-01, -1.43980721e-02, -3.13172730e-02, ...,
         1.08874582e-02,  5.92583223e-03, -2.64891884e-03],
       [-4.23054197e-01, -2.54839121e-02,  9.31803376e-03, ...,
         3.81143708e-04, -1.85049892e-03,  8.44598977e-04],
       [-4.39807192e-01, -5.47618522e-02,  2.98392643e-02, ...,
        -1.41145262e-03, -4.28496749e-03, -3.35354110e-03],
       ...,
       [-7.91771766e-01, -2.91518231e-02,  2.99255847e-02, ...,
         2.23143464e-03, -1.60545414e-04, -7.31051891e-03],
       [-8.51363125e-01, -3.06041730e-17,  2.01113137e-16, ...,
         3.28776259e-17,  1.39904791e-18, -2.79809582e-18],
       [-8.51363125e-01, -3.06041730e-17,  2.01113137e-16, ...,
         3.28776259e-17,  1.39904791e-18, -2.79809582e-18]])